In [41]:
#@hidden_cell
# The project token is an authorization token that is used to access project resources like data sources, connections, and used by platform APIs.
from project_lib import Project

LIMIT = 100 # A default Foursquare API limit value

print('CLIENT_ID: ')
#print('CLIENT_SECRET:' + CLIENT_SECRET)


CLIENT_ID: 


In [2]:
#Capstone Project Coursera
#import libraries
import matplotlib.pyplot as plt
from unicodedata import normalize
#scrape wikipedia page for Toronto data
! pip install requests beautifulsoup4
from bs4 import BeautifulSoup
!pip install folium
import requests # library to handle requests
import pandas as pd # library for data analsysis
import numpy as np # library to handle data 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
# import k-means from clustering stage
from sklearn.cluster import KMeans

!pip install geopy
from geopy.geocoders import Nominatim # module to convert an address into latitude and longitude values

# libraries for displaying images
from IPython.display import Image 
from IPython.core.display import HTML 
    
#! pip install folium==0.5.0
import folium # plotting library
print('Libraries imported.')

Libraries imported.


In [3]:
#print hello message
print("Hello Capstone Project Course!")

Hello Capstone Project Course!


In [4]:
#reading in geospacial data
import pandas as pd
geodata = pd.read_csv('https://cocl.us/Geospatial_data')
playground = geodata

In [5]:
#scrape wikipedia page for toronto neighborhood list
table_NM = pd.read_html('https://en.wikipedia.org/wiki/Demographics_of_Toronto_neighbourhoods')

In [6]:
#scrape webpage for list of postal codes in canada to dataframe
table = pd.read_html("https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M",skiprows=0)
pc_data = table[0]
pc_data.tail()

Postal Code       Borough  \
175         M5Z  Not assigned   
176         M6Z  Not assigned   
177         M7Z  Not assigned   
178         M8Z     Etobicoke   
179         M9Z  Not assigned   

                                         Neighbourhood  
175                                       Not assigned  
176                                       Not assigned  
177                                       Not assigned  
178  Mimico NW, The Queensway West, South of Bloor,...  
179                                       Not assigned

In [7]:
#remove those with fields containing 'not assigned'
pc_data = pc_data[pc_data.Neighbourhood != 'Not assigned']
pc_data.head()

Postal Code           Borough                                Neighbourhood
2         M3A        North York                                    Parkwoods
3         M4A        North York                             Victoria Village
4         M5A  Downtown Toronto                    Regent Park, Harbourfront
5         M6A        North York             Lawrence Manor, Lawrence Heights
6         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [8]:
#copy duplicate column data if not assigned
pc_data.is_copy=False
pc_data['Neighbourhood'] = np.where(pc_data['Neighbourhood'].values == 'Not assigned',
                                  pc_data['Borough'],
                                  pc_data['Neighbourhood']                                 
                                 )
pc_data.head(5)

/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/ipykernel/__main__.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


Postal Code           Borough                                Neighbourhood
2         M3A        North York                                    Parkwoods
3         M4A        North York                             Victoria Village
4         M5A  Downtown Toronto                    Regent Park, Harbourfront
5         M6A        North York             Lawrence Manor, Lawrence Heights
6         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [9]:
#more than one neighborhood can exist - combine
comb = pc_data.groupby(['Postal Code', 'Borough'])['Neighbourhood'].apply(lambda x: "%s" % ', '.join(x))
#convert into dataframe
comb = comb.to_frame().reset_index()
comb.head(5)

Postal Code      Borough                           Neighbourhood
0         M1B  Scarborough                          Malvern, Rouge
1         M1C  Scarborough  Rouge Hill, Port Union, Highland Creek
2         M1E  Scarborough       Guildwood, Morningside, West Hill
3         M1G  Scarborough                                  Woburn
4         M1H  Scarborough                               Cedarbrae

In [10]:
zip_geo = pc_data.set_index('Postal Code').join(playground.set_index('Postal Code')).reset_index()
zip_geo.shape

(103, 5)

In [11]:
zip_geo.columns = ['PostalCode', 'Borough', 'Neighbourhood', 'Latitude', 'Longitude']
zip_geo.head(5)

PostalCode           Borough                                Neighbourhood  \
0        M3A        North York                                    Parkwoods   
1        M4A        North York                             Victoria Village   
2        M5A  Downtown Toronto                    Regent Park, Harbourfront   
3        M6A        North York             Lawrence Manor, Lawrence Heights   
4        M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  
0  43.753259 -79.329656  
1  43.725882 -79.315572  
2  43.654260 -79.360636  
3  43.718518 -79.464763  
4  43.662301 -79.389494

In [12]:
!wget -q -O 'canada_geo.csv' http://cocl.us/Geospatial_data
print('Done!')

Done!


In [13]:
geo = pd.read_csv('canada_geo.csv')
geo.head(5)

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [14]:
table_EY = pd.read_html('https://en.wikipedia.org/wiki/Demographics_of_Toronto_neighbourhoods')
len(table_EY)
df = table_EY
df.pop(0)

0                                                  1
0 NaN  This article's factual accuracy may be comprom...

In [15]:
city = 'TORONTO, ON'

geo = Nominatim(user_agent="geopy.geocoders.options.default_user_agent")
location = geo.geocode(city)
lat= location.latitude
long = location.longitude
print('Coordinates of Toronto are {}, {}.'.format(lat, long))

Coordinates of Toronto are 43.6534817, -79.3839347.


In [16]:
#create map
mapt = folium.Map(location=[lat, long], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(zip_geo['Latitude'], zip_geo['Longitude'], zip_geo['Borough'], zip_geo['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.5,
        parse_html=False).add_to(mapt)  
    
mapt

In [17]:
zip_geo.loc[1, 'Neighbourhood']

'Victoria Village'

In [18]:
neighborhood_latitude = zip_geo.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = zip_geo.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = zip_geo.loc[0, 'Neighbourhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Parkwoods are 43.7532586, -79.3296565.


In [19]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url 


'https://api.foursquare.com/v2/venues/explore?&client_id=L24KHHW5WMQCKAIRHFX25QADRKXB2EAJEV2EB00T3NI4P4GH&client_secret=B5A5IIYFKQZT5MVXBF1J3RRQ2W0NAVOQBJ2HCHHOQDQWG0H0&v=20180605&ll=43.7532586,-79.3296565&radius=500&limit=100'

In [20]:
results = requests.get(url).json()


In [21]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [22]:
import json
import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

In [23]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/ipykernel/__main__.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  app.launch_new_instance()


name         categories        lat        lng
0  Brookbanks Park               Park  43.751976 -79.332140
1    Variety Store  Food & Drink Shop  43.751974 -79.333114
2    GreenWin pool               Pool  43.756232 -79.333842

In [24]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [25]:
toronto = getNearbyVenues(names=zip_geo['Neighbourhood'],
                          latitudes=zip_geo['Latitude'],
                          longitudes=zip_geo['Longitude'],
                                )


Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Queen's Park, Ontario Provincial Government
Islington Avenue, Humber Valley Village
Malvern, Rouge
Don Mills
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
East Toronto, Broadview North (Old East York)
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birchmo

In [26]:
toronto.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                               5   
Alderwood, Long Branch                                                  8   
Bathurst Manor, Wilson Heights, Downsview North                        21   
Bayview Village                                                         4   
Bedford Park, Lawrence Manor East                                      24   
Berczy Park                                                            58   
Birch Cliff, Cliffside West                                             4   
Brockton, Parkdale Village, Exhibition Place                           24   
Business reply mail Processing Centre, South Ce...                     15   
CN Tower, King and Spadina, Railway Lands, Harb...                     17   
Caledonia-Fairbanks                                                     4   
Canada Post Gateway Processing Centre                                  13   
Cedarbrae                                                               8   
Central Bay Street                                                     65   
Christie                                                               16   
Church and Wellesley                                                   80   
Clarks Corners, Tam O'Shanter, Sullivan                                13   
Cliffside, Cliffcrest, Scarborough Village West                         3   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             34   
Davisville North                                                        8   
Del Ray, Mount Dennis, Keelsdale and Silverthorn                        4   
Don Mills                                                              24   
Dorset Park, Wexford Heights, Scarborough Town ...                      5   
Downsview                                                              15   
Dufferin, Dovercourt Village                                           15   
East Toronto, Broadview North (Old East York)                           2   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...                      9   
Fairview, Henry Farm, Oriole                                           62   
First Canadian Place, Underground city                                100   
Forest Hill North & West, Forest Hill Road Park                         4   
Garden District, Ryerson                                              100   
Glencairn                                                               4   
Golden Mile, Clairlea, Oakridge                                         9   
Guildwood, Morningside, West Hill                                       8   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          26   
Hillcrest Village                                                       5   
Humber Summit                                                           4   
Humberlea, Emery                                                        3   
Humewood-Cedarvale                                                      4   
India Bazaar, The Beaches West                                         21   
Kennedy Park, Ionview, East Birchmount Park                             5   
Kensington Market, Chinatown, Grange Park                              62   
Kingsview Village, St. Phillips, Martin Grove G...                      4   
Lawrence Manor, Lawrence Heights                                       14   
Lawrence Park                                                           4   
Leaside                                                                31   
Little Portugal, Trinity                                               42   
Malvern, Rouge                                                          2   
Milliken, Agincourt North, Steeles East, L'Amor.

In [27]:
# one hot encoding
canada_onehot = pd.get_dummies(toronto[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
canada_onehot['Neighborhood'] = toronto['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [canada_onehot.columns[-1]] + list(canada_onehot.columns[:-1])
canada_onehot = canada_onehot[fixed_columns]

canada_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Airport  \
0            0                  0               0        0   
1            0                  0               0        0   
2            0                  0               0        0   
3            0                  0               0        0   
4            0                  0               0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auto Garage  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0            0          0           0           0       0     0    0   
1            0          0           0           0       0     0    0   
2            0          0           0           0       0     0    0   
3            0          0           0           0       0     0    0   
4            0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Basketball Stadium  \
0               0                 0                 0                   0   
1               0                 0                 0                   0   
2               0                 0                 0                   0   
3               0                 0                 0                   0   
4               0                 0                 0                   0   

   Beach  Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  \
0      0                0         0           0                   0   
1      0                0         0           0                   0   
2      0                0         0           0                   0   
3      0                0         0           0                   0   
4      0                0         0           0                   0   

   Bike Shop  Bistro  Boat or Ferry  Bookstore  Boutique  \
0          0       0              0          0         0   
1          0       0              0          0         0   
2          0       0              0          0         0   
3          0       0              0          0         0   
4          0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0                0         0             0              0         0   
1                0         0        

In [28]:
c_grouped = canada_onehot.groupby('Neighborhood').mean().reset_index()
c_grouped

Neighborhood  Yoga Studio  \
0                                           Agincourt     0.000000   
1                              Alderwood, Long Branch     0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North     0.000000   
3                                     Bayview Village     0.000000   
4                   Bedford Park, Lawrence Manor East     0.000000   
5                                         Berczy Park     0.000000   
6                         Birch Cliff, Cliffside West     0.000000   
7        Brockton, Parkdale Village, Exhibition Place     0.041667   
8   Business reply mail Processing Centre, South C...     0.000000   
9   CN Tower, King and Spadina, Railway Lands, Har...     0.000000   
10                                Caledonia-Fairbanks     0.000000   
11              Canada Post Gateway Processing Centre     0.000000   
12                                          Cedarbrae     0.000000   
13                                 Central Bay Street     0.015385   
14                                           Christie     0.000000   
15                               Church and Wellesley     0.025000   
16            Clarks Corners, Tam O'Shanter, Sullivan     0.000000   
17    Cliffside, Cliffcrest, Scarborough Village West     0.000000   
18                     Commerce Court, Victoria Hotel     0.000000   
19                                         Davisville     0.000000   
20                                   Davisville North     0.000000   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn     0.000000   
22                                          Don Mills     0.000000   
23  Dorset Park, Wexford Heights, Scarborough Town...     0.000000   
24                                          Downsview     0.000000   
25                       Dufferin, Dovercourt Village     0.000000   
26      East Toronto, Broadview North (Old East York)     0.000000   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...     0.000000   
28                       Fairview, Henry Farm, Oriole     0.000000   
29             First Canadian Place, Underground city     0.000000   
30    Forest Hill North & West, Forest Hill Road Park     0.000000   
31                           Garden District, Ryerson     0.000000   
32                                          Glencairn     0.000000   
33                    Golden Mile, Clairlea, Oakridge     0.000000   
34                  Guildwood, Morningside, West Hill     0.000000   
35  Harbourfront East, Union Station, Toronto Islands     0.000000   
36                      High Park, The Junction South     0.000000   
37                                  Hillcrest Village     0.000000   
38                                      Humber Summit     0.000000   
39                                   Humberlea, Emery     0.000000   
40                                 Humewood-Cedarvale     0.000000   
41                     India Bazaar, The Beaches West     0.000000   
42        Kennedy Park, Ionview, East Birchmount Park     0.000000   
43          Kensington Market, Chinatown, Grange Park     0.000000   
44  Kingsview Village, St. Phillips, Martin Grove ...     0.000000   
45                   Lawrence Manor, Lawrence Heights     0.000000   
46                                      Lawrence Park     0.000000   
47                                            Leaside     0.000000   
48                           Little Portugal, Trinity     0.023810   
49                                     Malvern, Rouge     0.000000   
50  Milliken, Agincourt North, Steeles East, L'Amo...     0.000000   
51  Mimico NW, The Queensway West, South of Bloor,...     0.000000   
52                        Moore Park, Summerhill East     0.000000   
53       New Toronto, Mimico South, Humber Bay Shores     0.000000   
54           North Park, Maple Leaf Park, Upwood Park     0.000000   
55                  North Toronto West, Lawrence Park     0.058824   
56                Northwest, West Humber - Clairvil

In [29]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [30]:
#top 10 venues
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = c_grouped['Neighborhood']

for ind in np.arange(c_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(c_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                                        Agincourt                Lounge   
1                           Alderwood, Long Branch           Pizza Place   
2  Bathurst Manor, Wilson Heights, Downsview North                  Bank   
3                                  Bayview Village                  Café   
4                Bedford Park, Lawrence Manor East        Sandwich Place   

       2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0  Latin American Restaurant          Skating Rink        Clothing Store   
1                        Gym              Pharmacy                   Pub   
2                Coffee Shop         Shopping Mall         Deli / Bodega   
3                       Bank    Chinese Restaurant   Japanese Restaurant   
4                Coffee Shop    Italian Restaurant      Sushi Restaurant   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0        Breakfast Spot             Drugstore        Discount Store   
1        Sandwich Place          Dance Studio           Coffee Shop   
2           Supermarket        Ice Cream Shop      Sushi Restaurant   
3         Women's Store                 Diner        Discount Store   
4   Japanese Restaurant               Butcher                  Café   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0   Distribution Center               Dog Run       Doner Restaurant  
1             Drugstore            Donut Shop       Doner Restaurant  
2            Restaurant    Chinese Restaurant    Fried Chicken Joint  
3   Distribution Center               Dog Run       Doner Restaurant  
4     Indian Restaurant                   Spa             Restaurant

In [31]:
#lets cluster by k means
# set number of clusters
kclusters = 5

c_grouped_clustering = c_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(c_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]


array([4, 4, 4, 4, 4, 4, 4, 4, 4, 4], dtype=int32)

In [32]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluser Labels', kmeans.labels_)

c_merged = toronto

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
c_merged = c_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

c_merged.head() # check the last columns!

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2         Parkwoods              43.753259              -79.329656   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2           GreenWin pool       43.756232       -79.333842   
3  Victoria Village Arena       43.723481       -79.315635   
4               Portugril       43.725819       -79.312785   

          Venue Category  Cluser Labels  1st Most Common Venue  \
0                   Park              0                   Park   
1      Food & Drink Shop              0                   Park   
2                   Pool              0                   Park   
3           Hockey Arena              4  Portuguese Restaurant   
4  Portuguese Restaurant              4  Portuguese Restaurant   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0     Food & Drink Shop                  Pool     Electronics Store   
1     Food & Drink Shop                  Pool     Electronics Store   
2     Food & Drink Shop                  Pool     Electronics Store   
3          Hockey Arena     French Restaurant           Coffee Shop   
4          Hockey Arena     French Restaurant           Coffee Shop   

         5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0  Eastern European Restaurant             Drugstore            Donut Shop   
1  Eastern European Restaurant             Drugstore            Donut Shop   
2  Eastern European Restaurant             Drugstore            Donut Shop   
3           Dim Sum Restaurant                 Diner        Discount Store   
4           Dim Sum Restaurant                 Diner        Discount Store   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0      Doner Restaurant         Deli / Bodega                Dog Run  
1      Doner Restaurant         Deli / Bodega                Dog Run  
2      Doner Restaurant         Deli / Bodega                Dog Run  
3   Distribution Center               Dog Run       Doner Restaurant  
4   Distribution Center               Dog Run       Doner Restaurant

In [33]:
import matplotlib.cm as cm
import matplotlib.colors as colors

In [34]:
# create map
map_clusters = folium.Map(location=[lat, long], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(c_merged['Venue Latitude'], c_merged['Venue Longitude'], c_merged['Neighborhood'], c_merged['Cluser Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [35]:
#let's look at cluster #1
c_merged.loc[c_merged['Cluser Labels'] == 0, c_merged.columns[[1] + list(range(5, c_merged.shape[1]))]]

Neighborhood Latitude  Venue Longitude     Venue Category  \
0                 43.753259       -79.332140               Park   
1                 43.753259       -79.333114  Food & Drink Shop   
2                 43.753259       -79.333842               Pool   
415               43.689026       -79.456300               Park   
416               43.689026       -79.456333      Women's Store   
417               43.689026       -79.448922               Pool   
418               43.689026       -79.448924               Park   
772               43.685347       -79.335007               Park   
773               43.685347       -79.335007  Convenience Store   
1240              43.789053       -79.410022               Park   
1369              43.752758       -79.401393  Convenience Store   
1370              43.752758       -79.399717               Park   
1684              43.815252       -79.281716       Intersection   
1685              43.815252       -79.289773               Park   
1686              43.815252       -79.289867         Playground   
1754              43.679563       -79.378934         Playground   
1755              43.679563       -79.373788               Park   
1756              43.679563       -79.382773               Park   
1757              43.679563       -79.373842              Trail   

      Cluser Labels 1st Most Common Venue 2nd Most Common Venue  \
0                 0                  Park     Food & Drink Shop   
1                 0                  Park     Food & Drink Shop   
2                 0                  Park     Food & Drink Shop   
415               0                  Park                  Pool   
416               0                  Park                  Pool   
417               0                  Park                  Pool   
418               0                  Park                  Pool   
772               0                  Park     Convenience Store   
773               0                  Park     Convenience Store   
1240              0                  Park      Department Store   
1369              0                  Park     Convenience Store   
1370              0                  Park     Convenience Store   
1684              0                  Park          Intersection   
1685              0                  Park          Intersection   
1686              0                  Park          Intersection   
1754              0                  Park            Playground   
1755              0                  Park            Playground   
1756              0                  Park            Playground   
1757              0                  Park            Playground   

     3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
0                     Pool     Electronics Store  Eastern European Restaurant   
1                     Pool     Electronics Store  Eastern European Restaurant   
2                     Pool     Electronics Store  Eastern European Restaurant   
415          Women's Store          Gourmet Shop         Ethiopian Restaurant   
416          Women's Store          Gourmet Shop         Ethiopian Restaurant   
417          Women's Store          Gourmet Shop         Ethiopian Restaurant   
418          Women's Store          Gourmet Shop         Ethiopian Restaurant   
772            Event Space  Ethiopian Restaurant                  Escape Room   
773            Event Space  Ethiopian Restaurant                  Escape Room   
1240           Event Space  Ethiopian Restaurant                  Escape Room   
1369           Event Space  Ethiopian Restaurant                  Escape Room   
1370           Event Space  Ethiopian Restaurant                  Escape Room   
1684            Playground      Doner Restaurant           Dim Sum Restaurant   
1685            Playground      Doner Restaurant           Dim Sum Restaurant   
1686            Playground      Doner Restaurant           Dim Sum Restaurant   
1754                 Trail  

In [36]:
#let's look at cluster #2
c_merged.loc[c_merged['Cluser Labels'] == 1, c_merged.columns[[1] + list(range(5, c_merged.shape[1]))]]

Neighborhood Latitude  Venue Longitude            Venue Category  \
419               43.770992       -79.221156               Coffee Shop   
420               43.770992       -79.223078               Coffee Shop   
421               43.770992       -79.214502     Korean BBQ Restaurant   
1478              43.636966       -79.618721                     Hotel   
1479              43.636966       -79.620580             Burrito Place   
1480              43.636966       -79.616829               Coffee Shop   
1481              43.636966       -79.615600                     Hotel   
1482              43.636966       -79.620575       Fried Chicken Joint   
1483              43.636966       -79.620879            Sandwich Place   
1484              43.636966       -79.621030               Coffee Shop   
1485              43.636966       -79.621405               Coffee Shop   
1486              43.636966       -79.618756       American Restaurant   
1487              43.636966       -79.620840  Mediterranean Restaurant   
1488              43.636966       -79.621021               Gas Station   
1489              43.636966       -79.621098              Intersection   
1490              43.636966       -79.621765                       Gym   

      Cluser Labels 1st Most Common Venue  2nd Most Common Venue  \
419               1           Coffee Shop  Korean BBQ Restaurant   
420               1           Coffee Shop  Korean BBQ Restaurant   
421               1           Coffee Shop  Korean BBQ Restaurant   
1478              1           Coffee Shop                  Hotel   
1479              1           Coffee Shop                  Hotel   
1480              1           Coffee Shop                  Hotel   
1481              1           Coffee Shop                  Hotel   
1482              1           Coffee Shop                  Hotel   
1483              1           Coffee Shop                  Hotel   
1484              1           Coffee Shop                  Hotel   
1485              1           Coffee Shop                  Hotel   
1486              1           Coffee Shop                  Hotel   
1487              1           Coffee Shop                  Hotel   
1488              1           Coffee Shop                  Hotel   
1489              1           Coffee Shop                  Hotel   
1490              1           Coffee Shop                  Hotel   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
419          Women's Store            Donut Shop                 Diner   
420          Women's Store            Donut Shop                 Diner   
421          Women's Store            Donut Shop                 Diner   
1478                   Gym        Sandwich Place          Intersection   
1479                   Gym        Sandwich Place          Intersection   
1480                   Gym        Sandwich Place          Intersection   
1481                   Gym        Sandwich Place          Intersection   
1482                   Gym        Sandwich Place          Intersection   
1483                   Gym        Sandwich Place          Intersection   
1484                   Gym        Sandwich Place          Intersection   
1485                   Gym        Sandwich Place          Intersection   
1486                   Gym        Sandwich Place          Intersection   
1487                   Gym        Sandwich Place          Intersection   
1488                   Gym        Sandwich Place          Intersection   
1489                   Gym        Sandwich Place          Intersection   
1490                   Gym        Sandwich Place          Intersection   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
419         Discount Store   Distribution Center               Dog Run   
420         Discount Store   Distribution Center               Dog Run   
421         Discount Store   Distribution Center               Dog Run   
1478           Gas Station         

In [37]:
#let's look at cluster #3
c_merged.loc[c_merged['Cluser Labels'] == 2, c_merged.columns[[1] + list(range(5, c_merged.shape[1]))]]

Neighborhood Latitude  Venue Longitude Venue Category  Cluser Labels  \
2013              43.653654       -79.501702          River              2   

     1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
2013                 River      Doner Restaurant          Dessert Shop   

     4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
2013    Dim Sum Restaurant                 Diner        Discount Store   

     7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
2013   Distribution Center               Dog Run            Donut Shop   

     10th Most Common Venue  
2013            College Gym

In [38]:
#let's look at cluster #4
c_merged.loc[c_merged['Cluser Labels'] == 3, c_merged.columns[[1] + list(range(5, c_merged.shape[1]))]]

Neighborhood Latitude  Venue Longitude Venue Category  Cluser Labels  \
1363              43.706876       -79.516102  Jewelry Store              3   

     1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
1363         Jewelry Store             Drugstore                 Diner   

     4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
1363        Discount Store   Distribution Center               Dog Run   

     7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
1363      Doner Restaurant            Donut Shop         Women's Store   

     10th Most Common Venue  
1363   Fast Food Restaurant

In [39]:
#let's look at cluster #5
c_merged.loc[c_merged['Cluser Labels'] == 4, c_merged.columns[[1] + list(range(5, c_merged.shape[1]))]]

Neighborhood Latitude  Venue Longitude                   Venue Category  \
3                 43.725882       -79.315635                     Hockey Arena   
4                 43.725882       -79.312785            Portuguese Restaurant   
5                 43.725882       -79.313103                      Coffee Shop   
6                 43.725882       -79.317418                French Restaurant   
7                 43.654260       -79.362017                           Bakery   
8                 43.654260       -79.361809                      Coffee Shop   
9                 43.654260       -79.358008              Distribution Center   
10                43.654260       -79.361149                   Breakfast Spot   
11                43.654260       -79.359874                              Spa   
12                43.654260       -79.356980                       Restaurant   
13                43.654260       -79.359725             Gym / Fitness Center   
14                43.654260       -79.356211                             Park   
15                43.654260       -79.359323                    Historic Site   
16                43.654260       -79.358127                   Chocolate Shop   
17                43.654260       -79.361832                   Farmers Market   
18                43.654260       -79.364503                   Breakfast Spot   
19                43.654260       -79.361442                      Coffee Shop   
20                43.654260       -79.360723                     Dessert Shop   
21                43.654260       -79.359515                      Coffee Shop   
22                43.654260       -79.365609                      Coffee Shop   
23                43.654260       -79.358967                              Pub   
24                43.654260       -79.364917                      Coffee Shop   
25                43.654260       -79.357593            Performing Arts Venue   
26                43.654260       -79.354806                             Park   
27                43.654260       -79.357843                French Restaurant   
28                43.654260       -79.358709                           Bakery   
29                43.654260       -79.362195                             Park   
30                43.654260       -79.359539                           Bakery   
31                43.654260       -79.365873                      Event Space   
32                43.654260       -79.357078                      Coffee Shop   
33                43.654260       -79.364955                      Yoga Studio   
34                43.654260       -79.358849                             Café   
35                43.654260       -79.358920               Mexican Restaurant   
36                43.654260       -79.364753                          Theater   
37                43.654260       -79.358862                             Café   
38                43.654260       -79.357615                          Theater   
39                43.654260       -79.356503                             Café   
40                43.654260       -79.359436                       Shoe Store   
41                43.654260       -79.354662                              Pub   
42                43.654260       -79.358489                              Pub   
43                43.654260       -79.360073                          Brewery   
44                43.654260       -79.361222                      Art Gallery   
45                43.654260       -79.361005                   Cosmetics Shop   
46                43.654260       -79.359667                Electronics Store   
47                43.654260       -79.357463                       Beer Store   
48                43.654260       -79.356336                             Bank   
49                43.654260       -79.358970                      Coffee Shop   
50                43.654260       -79.358917                       Restaurant   
51                43.654260       -79